# CNN starter kit

Let us tackle this problem using a CNN model.

First, note, in my setup, all the images are in the `unzip` directory and data files in the `data` directory. The following parameters prepare you for that but may need to be customised to your environment. My local environmet looks like this
- unzip
  - planet-dec17
    - ... lots of `png` images
  - planet-dec18
    - ... lots of `png` images
  - planet-jun18
    - ... lots of `png` images
  - planet-jun18
    - ... lots of `png` images
  -sentinel
    - ... lots of `tif` images
- data
  - auxilary_data_unique.csv
  - extra_train.csv
  - test.csv
  - train-unique.csv

Note that I placed all images into the directories as noted above and this allows me to easily access them without any gymnastics around the many different sets that were published over time.

## License

MG Ferreira<br/>
&copy; Ferra Solutions (Pty) Ltd https://www.ferrasolutions.com</br>
Note that this is *copyrighted* material.

You are welcome to use it to compete, but you can not publish this notebook elsewhere as if you created it, or use it in e.g. a lecture or as part of a paper or in some other setting without written permission from me.

## Disclaimer

This is a fairly elaborate example meant to get you going.

I created this because I was asked by some of the other contestants to do it and do so to help newcomers get going really quickly.

I wish I had this at the outset but, you know what, I am also glad I did not because it forced me to learn all these things.

Being an example, it is not meant for production use nor are there *any* guarantees of usability of correctness included with it.

## Warning

This will estimate a CNN model and then write the outputs in a submission ready file to

`cnn.csv`

without asking for permission. If you have such a file then you will loose it if you run this.

This is also covered by the disclaimer - if this notebook formats your hard disk you have been warned. But don't worry, it has good intentions, although things may heat up a bit during the model estimation process later :-)

In [ ]:
# Data paths - customise for your environment
data_path = 'data'
img_path  = 'unzip'

# Load libraries

Now let us load all the required libraries

In [ ]:
import math
import os
import random

import skimage.io

import pandas     as pd
import numpy      as np
import tensorflow as tf

from tensorflow.keras        import layers
from tensorflow.keras.models import Model

# Utilities

Next let us define a few utility functions and also functions to load RGB. Note especially the `load_rgb_stack` function which will load the RGB and return it as a stack with 12 channels (RGB x 4 photos).

In [ ]:
# Load the training and auxilliary data
def load_data ():

    train = pd.read_csv ( f'{ data_path }/train-unique.csv' )
    aux   = pd.read_csv ( f'{ data_path }/auxilary_data-unique.csv' )
    extra = pd.read_csv ( f'{ data_path }/extra_train.csv' )

    return pd.concat ( [ train, aux, extra ] )

# Load the test data
def load_test ():

    return pd.read_csv ( f'{ data_path }/test.csv' )

# Supplied - load RGB image
def load_RGB_images ( ID ):

    # e.g id_0b242e06 -> 0b242e06
    name      = ID.split('_')[1]

    img_jun17 = skimage.io.imread ( f'{img_path}/planet-jun17/{name}.png' )
    img_dec17 = skimage.io.imread ( f'{img_path}/planet-dec17/{name}.png' )
    img_jun18 = skimage.io.imread ( f'{img_path}/planet-jun18/{name}.png' )
    img_dec18 = skimage.io.imread ( f'{img_path}/planet-dec18/{name}.png' )

    return img_jun17, img_dec17, img_jun18, img_dec18

# Load the RGB mages and return them as a stack
def load_rgb_stack ( ID ):

    rgbs = load_RGB_images ( ID )
    return np.concatenate ( [ rgbs [ 0 ], rgbs [ 1 ], rgbs [ 2 ], rgbs [ 3 ] ], axis = 2 )

# Spectral images

The spectal images are next. They are treated similarly. Note that there are 192 channels, 16 channels for each of 12 photos. Since channels 14, 15 and 16 are not important they are discarded below. Note that, since the channels here are zero-based, the channels removed in the code becomes 13, 14 and 15.

## Interesting channels

Some preliminary investigation revealed that channels 3, 13, 49, 50, 66, 117, 119, 121, 122, 133, 136 and 139 are *interesting*. These channels show a significant difference in the pixels inside the plot and those outside. For that reason the code below includes this array of channels. This allows for it to be easily extracted later.

In [ ]:
# Supplied - load spectral image
def load_Spectral_image ( ID ):

    # e.g id_0b242e06 -> 0b242e06
    name         = ID.split ( '_' ) [ 1 ]
    img_sentinel = skimage.io.imread ( f'{img_path}/sentinel/{name}.tif' )

    return img_sentinel

# Channels we want to remove from spectral image
# We are not interested in channel 13, 14 or 15
sr13 = [ i for i in range ( 13, 192, 16 ) ]
sr14 = [ i for i in range ( 14, 192, 16 ) ]
sr15 = [ i for i in range ( 15, 192, 16 ) ]

sral = sr13
sral.extend ( sr14 )
sral.extend ( sr15 )

# Spectral channels we find interesting
sintch = [ 3, 13, 49, 50, 66, 117, 119, 121, 122, 133, 136, 139 ] 

# Read the spectral image and remove the unused channels from it
def load_spectral_stack ( ID ):

    return np.delete ( load_Spectral_image ( ID ), sral, axis = 2 )

# Review

Let us build a CNN with three legs.
 - One leg will handle the black and white satellite images.
 - One leg will handle the spectral images, specifically the channels we find interesting.
 - Finally a leg to handle meta data such as the year and the size of the plot.

Later we will combine all three these legs into a dense network and then use that to predict the target location.

## Prepocessing

Based on the review, we need to do the following.
 - Convert the 4 RGB images to B&W and collate them into 4 channels
   - When we convert the images to grayscale they will also be scaled to between 0-1
 - Extract the spectral channels we are interested in
   - We need to rescale them, let us calculate and use the z-scores
 - Scale and relocate the metadata so that it is between 0 and 1
   - Note that the average yield is 0.33 (you can easily verify this using a spreadsheet)
   - We will also use the yield and will use this value when the yield is missing

We also need to resize the images so that they are all the same size. Let us use 80x80 for the RGB and 40x40 for the spectral images.

Then we need to rescale the target as well. We will use a `tanh` activation which lies between -1 and +1. Since the field values are between -2 and 2, we need to also preprocess the targets.

Importantly, we also need to create a validation sample so that we can test how well our model works.

This leads to the utilities below.

In [ ]:
from skimage.color import rgb2gray
from skimage.transform import resize

# Preprocess the RGB
def preprocess_rgb ( row ):

    # Load the RGB stack
    rgb = load_rgb_stack ( row.ID )

    # Convert to B&W
    # and rescale to 0 .. 1
    bw1 = rgb2gray ( rgb [ :, :, 0:3 ] )
    bw2 = rgb2gray ( rgb [ :, :, 3:6 ] )
    bw3 = rgb2gray ( rgb [ :, :, 6:9 ] )
    bw4 = rgb2gray ( rgb [ :, :, 9:12 ] )

    # Stack
    bw_stack = np.dstack ( [ bw1, bw2, bw3, bw4 ] )

    # Rescale and return
    return resize ( bw_stack, [ 80, 80 ] ).flatten ()

# Preprocess the spectral
def preprocess_spc ( row ):

    # Load the spectral stack - here channels 13, 14 and 15 have already been removed
    spc = load_spectral_stack ( row.ID )

    # Retain only the ones we are interested in
    spc = spc [ :, :, sintch ]

    # Convert to z-score
    for ch in range ( spc.shape [ 2 ] ):
        m = spc [ :, :, ch ].mean ()
        s = spc [ :, :, ch ].std ()
        spc [ :, :, ch ] = ( spc [ :, :, ch ] - m ) / s
    
    # Resize and return
    return resize ( spc, [ 40, 40 ] ).flatten ()

# Preprocess the metadata
def preprocess_meta ( row ):

    year = int ( row.Year )
    size = float ( row.PlotSize_acres )
    yld  = float ( row.Yield )

    # Replace the yield with the average if not available
    if np.isnan ( yld ):
        yld = 0.33

    # Scale the year
    year = ( year - 2015 ) / 5

    # Done
    return np.array ( [ year, size, yld ] )

# Preprocess the target
def preprocess_target ( row ):

    return np.array ( [ float ( row.x ) / 2, float ( row.y ) / 2 ] )

# Preprocess a whole row
def preprocess_row ( row ):

    return np.concatenate ( [ preprocess_rgb ( row ), preprocess_spc ( row ), preprocess_meta ( row ), preprocess_target ( row ) ] )

# Later we will also preprocess a row from the test set where there is no knowledge of the target
def preprocess_test ( row ):

    return np.concatenate ( [ preprocess_rgb ( row ), preprocess_spc ( row ), preprocess_meta ( row ) ] )

# Random seed

Since we must be able to reproduce the results, we also need a utility to set the random seed.

In [ ]:
# Set the random seed
def set_random_seed ( seed ):

    os.environ [ 'PYTHONHASHSEED' ] = str ( seed )
    np.random.seed ( seed )

    if tf.__version__ > '1.':
        tf.random.set_seed ( seed )
    else:
        tf.set_random_seed ( seed )

    random.seed ( seed )

    return

# Train and validation samples

Now we are ready and we can extract the data.

Each row in our dataset will have the following structure.
 - `80 x 80 x 4` for the B&W images
 - `40 x 40 x len ( sintch )` for the interesting spectral images
 - `len ( meta )` for the metadata
 - `len ( target ) = 2` for the target
   - this means that the target `x` sits at `[ :, -3 ]` and the target `y` sits at `[ :, -2 ]`
   - this is important for later on when we slice up the store to train our network
 - 1 additional column
   - this column will be 1 if the row is in the training and 0 if in the validation sample
   - we will mark this randomly so that roughly 20% of the data ends up in the validation sample
   - a lot of slicing will be performed on this last column, which, importantly, now finds itself at `[ :, -1 ]`

We also profile this section as it will take a while to complete.

In [ ]:
%%time

# Some counts
n_rgb    = 80 * 80 * 4
n_spc    = 40 * 40 * len ( sintch )
n_meta   = 3
n_target = 2
n_valid  = 1

n_inputs = n_rgb + n_spc + n_meta
n_all    = n_inputs + n_target + n_valid

# Set the random seed
set_random_seed ( 20210618 )

# Load the training data
data  = load_data ()

# Prepare an array where we will store our data
store = np.zeros ( [ data.shape [ 0 ], n_all ], dtype = float )

# Now load the data into this
i = 0
for irow, row in data.iterrows ():

    # Load the preprocessed data
    store [ i, :n_all - 1 ] = preprocess_row ( row )

    # Set the validation sample - 20% change of being in the validation sample
    if random.randint ( 0, 100 ) > 20:

        store [ i, -1 ] = 1

    # Move to next row
    i = i + 1


# Model

It is time to create our model.

It has an input layer that contains the full row. This is then cropped into the three parts (RGB, spectral and metadata). Each of these are then modelled separately.

The RGB is pooled until it is 20x20, as is the spectral. These two 20x20 images are then combined into a single, multichannel image which is processed further.

Finally the image as well as the metadata is concatenated into a dense network which has two tanh outputs.

In [ ]:
# Some parameters for what follows
padding = "same"

# Utility to create and return a CNN 2d convolution layer
#   features     - int giving number of features
#   kernel_size  - int giving size of kernel
#   activation   - string giving name of activation e.g. tanh or relu
#   batch_normal - boolean True to add a batch normalization layer
#   max_pool     - int 0 for no or a number to add a max pooling layer
#   avg_pool     - int 0 for no or a number to add an average pooling layer
#   input_layer  - the input layer
# Return the output layer
def make_c2d_layer ( features, kernel_size, batch_normal, activation, max_pool, avg_pool, input_layer ):

    next_layer = layers.Conv2D ( features, kernel_size, activation = activation, padding = padding ) ( input_layer )

    if batch_normal:

        next_layer = layers.BatchNormalization () ( next_layer )

    if max_pool > 0:

        next_layer = layers.MaxPooling2D ( max_pool, padding = padding ) ( next_layer )

    if avg_pool > 0:

        next_layer = layers.AveragePooling2D ( avg_pool, padding = padding ) ( next_layer )

    return next_layer

# Start with the input layer
input_layer = layers.Input ( shape = n_inputs )

# Reshape so that we can crop it
flat_layer = layers.Reshape ( target_shape = ( n_inputs, 1 ) ) ( input_layer )

# Chop into the various sections
rgb_flat_layer = layers.Cropping1D ( cropping = ( 0, n_inputs - n_rgb ) ) ( flat_layer )
rgb_layer = layers.Reshape ( target_shape = ( 80, 80, 4 ) ) ( rgb_flat_layer )

spc_flat_layer = layers.Cropping1D ( cropping = ( n_rgb, n_inputs - n_rgb - n_spc ) ) ( flat_layer )
spc_layer = layers.Reshape ( target_shape = ( 40, 40, len ( sintch ) ) ) ( spc_flat_layer )

meta_layer = layers.Cropping1D ( cropping = ( n_rgb + n_spc, 0 ) ) ( flat_layer )
meta_flat_layer = layers.Flatten () ( meta_layer )

# The heart of the CNN is below

# Convolve the RGB

# Here it goes from 80x80x4 to 80x80x8
rgb_layer1 = make_c2d_layer (  8, 1, True, "relu", 0, 0, rgb_layer )

# Now from 80x80x8 to 40x40x16 using max pooling
rgb_layer2 = make_c2d_layer ( 16, 3, True, "relu", 2, 0, rgb_layer1 )

# Now from 40x40x16 to 20x20x32
rgb_layer3 = make_c2d_layer ( 32, 3, True, "relu", 2, 0, rgb_layer2 )

# Convolve the spectral side

# Here it goes from 40x40xlen(sintch) to 40x40x16
spc_layer1 = make_c2d_layer ( 16, 1, True, "relu", 0, 0, spc_layer )

# Next from 40x40x16 to 20x20x32
spc_layer2 = make_c2d_layer ( 32, 3, True, "relu", 2, 0, spc_layer1 )

# Now we combine the two images and we have 20x20x64
img_layer = layers.Concatenate () ( [ rgb_layer3, spc_layer2 ] )

# Convolve this combined layer
img_layer1 = make_c2d_layer ( 64, 1, True, "relu", 0, 0, img_layer )

# Convolve again into 10x10 with 128 features
img_layer2 = make_c2d_layer ( 128, 3, True, "relu", 2, 0, img_layer1 )

# Now we flatten this and add the meta data
img_flat_layer = layers.Flatten () ( img_layer2 )

hidden_layer1 = layers.Concatenate () ( [ img_flat_layer, meta_flat_layer ] )

# Build a dense network on these
hidden_layer2 = layers.Dense ( 20, activation = "relu" ) ( hidden_layer1 )
hidden_layer3 = layers.Dense (  5, activation = "relu" ) ( hidden_layer2 )

# Now we can construct the output layer
output_layer = layers.Dense ( 2, activation = "tanh" ) ( hidden_layer3 )

# Construct the model
model = Model ( input_layer, output_layer )
model.summary ()

# Training time

The model is now built and we can train it on the training set. The elaborate `fit` below is to limit the data to those that were marked to be part of the training.

In [ ]:
%%time

# Now we can compile and train the model on the training set
model.compile ( optimizer = "SGD", loss = "mae" )
model.fit ( store [ store [ :, -1 ] == 1, :n_inputs ], store [ store [ :, -1 ] == 1, -3:-1 ], epochs = 10 )

# Testing time

With the model trained the next step is to test it.

Here we calculate the mean absolute deviation as that is the metric used in the competition. In the calculation below I add `abs x` to `abs y` and should therefore really divide the results by 2. But, since the targets have been scaled by 2, its omission below allows me to directly compare these results with the leaderboard. So a case of two wrongs making a right.

The stuff in the square brackets is to limit the sample to the training and validation sections.

In [ ]:
# Time to test the model
pred = model.predict ( store [ :, :n_inputs ] )

mae_0     = ( abs ( store [ :, -3 ] ) + abs ( store [ :, -2 ] ) ).mean ()
mae_full  = ( abs ( pred [                    :, 0 ] - store [                    :, -3 ] ) + abs ( pred [                    :, 1 ] - store [                    :, -2 ] ) ).mean ()
mae_train = ( abs ( pred [ store [ :, -1 ] == 1, 0 ] - store [ store [ :, -1 ] == 1, -3 ] ) + abs ( pred [ store [ :, -1 ] == 1, 1 ] - store [ store [ :, -1 ] == 1, -2 ] ) ).mean ()
mae_valid = ( abs ( pred [ store [ :, -1 ] == 0, 0 ] - store [ store [ :, -1 ] == 0, -3 ] ) + abs ( pred [ store [ :, -1 ] == 0, 1 ] - store [ store [ :, -1 ] == 0, -2 ] ) ).mean ()

print ( f"MAE zeros { mae_0 } full sample { mae_full } in-sample { mae_train } validation sample { mae_valid }" )

# Test and submit

The next step is to apply the model to the test data and create a submission file, as is done below.

In [ ]:
# Now we can run it on the test data and create a submission file at the same time

# Output file and file header
out = open ( "cnn.csv", "w" )
out.write ( "ID,x,y\n" )

# Test data
test = load_test ()

for irow, row in test.iterrows ():

    x = preprocess_test ( row )
    y = model ( x.reshape ( 1, -1 ) ).numpy ().flatten ()

    # Scale back to target and write result
    out.write ( str ( row.ID ) )
    out.write ( "," )
    out.write ( str ( y [ 0 ] * 2 ) )
    out.write ( "," )
    out.write ( str ( y [ 1 ] * 2 ) )
    out.write ( "\n" )

# Done
out.close ()

# Next steps

Well, do you feel lucky?

If so, then you can simply change the random seed and try again, hoping to come up with a better solution. Good luck with that.

Alternatively, you can try and train this differently or make minor changes here and there and see how it goes. Good luck with that as well.

More advanced would be to add a type of ResNet layer where you hook up earlier layers to the output. I discarded that idea here, although I use it in my own work, as it would simply blow up an already bloated example and because this really is to get newcomers going.

The best alternative, I think, is to really try to understand the problem and based on that understanding change this network into something better. This is more or less what I am doing. I had something like this roughly a month ago and since have changed it quite a bit based on my understanding of the problem.

That said, here the data is so dirty that you could easily be better of by just changing the seed here. The complexity I added since pales in comparison to the simplicity here.

# My approach

Yes - I do want to win and I hope by publishing this I am not endangering my chances.

As said, I started with this and this type of model remains one of my best thus far.

It scores 0.238 on the leaderboard and would put you, at the time of writing, in position 80 or so.

However, this does not *fully* solve the problem. To go into details at this stage will be premature, but I believe I've got a better grasp on this problem than is exibited in this model.

This model is a fairly standard CNN and it can be obviously improved by adding a ResNET type layer, but there are also some other refinements possible that are pretty problem specific. Those I will not divulge at this stage.

The advantages of the approach in this notebook is that it is simple, standard and it works well for this problem. The disadvantages is that it does not really solve the problem as it should and disregards important pieces of information which, again, I do not want to divulge right now.

I am working on another approach that I believe to be much better than this one, even though it looks pretty similar to this. The difference is based on customising this model more to the problem using some of the properties of CNNs that lend themselves to this type of customisation.

This other approach's advantages are that it is much more customised for the problem at hand and should solve it better if the data quality is better. Its disadvantages are that it is more complex, requires more work to transpose its outputs to the format required by the competition and that, for the data, it may not win this competition.

So this notebook gives you a real fighting chance, although I hope to be able to work my approach into a winning solution.

---

Regards<br/>
MG Ferreira<br/>
2021